<a href="https://colab.research.google.com/github/JamesPeralta/Gymnos/blob/master/NeuralNetwork/Iteration2/Model_Training_GPU.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# Gymnos Iteration 2
## Gymnos iteration 2 will use a single stream 2D convolutional neural network. For each video we will be passing in only one frame and the AIs prediction will be based on the single frame.



In [0]:
# You can list all of the hardware device running on your instance
from tensorflow.python.client import device_lib

local_devices = device_lib.list_local_devices()

for device in local_devices:
  print("_______________________________________\n" + str(device))

---
## Mount drive and download libraries from Github

In [1]:
from google.colab import drive
import os
import csv
import importlib
import datetime, os

# Load the TensorBoard notebook extension
!pip install -q tf-nightly-2.0-preview
%load_ext tensorboard

drive.mount('/content/drive')

     |████████████████████████████████| 88.0MB 532kB/s 
     |████████████████████████████████| 430kB 44.6MB/s 
     |████████████████████████████████| 61kB 30.3MB/s 
     |████████████████████████████████| 3.1MB 39.0MB/s 
ERROR: thinc 6.12.1 has requirement wrapt<1.11.0,>=1.10.0, but you'll have wrapt 1.11.1 which is incompatible.
Go to this URL in a browser: https://accounts.google.com/o/oauth2/auth?client_id=947318989803-6bn6qk8qdgf4n4g3pfee6491hc0brc4i.apps.googleusercontent.com&redirect_uri=urn%3Aietf%3Awg%3Aoauth%3A2.0%3Aoob&scope=email%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdocs.test%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fdrive.photos.readonly%20https%3A%2F%2Fwww.googleapis.com%2Fauth%2Fpeopleapi.readonly&response_type=code

Enter your authorization code:
··········
Mounted at /content/drive


In [2]:
# Retrieve the Data Generator Library
!curl "https://raw.githubusercontent.com/JamesPeralta/Gymnos/master/NeuralNetwork/Iteration2/GymnosDataGenerator_i2.py?token=AFLRMHIT4RFZHQ5SDU2AO5C46R3UY" >> GymnosDataGenerator_i2.py
# Retrieve the Helper Functions Library
!curl "https://raw.githubusercontent.com/JamesPeralta/Gymnos/master/NeuralNetwork/Iteration2/HelperFunctions_i2.py?token=AFLRMHOGFSXB6HZQO72HKXK46RK7O" >> HelperFunctions_i2.py

  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  5390  100  5390    0     0  19181      0 --:--:-- --:--:-- --:--:-- 19181
  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  6054  100  6054    0     0  45179      0 --:--:-- --:--:-- --:--:-- 45179


---
## Imports

In [3]:
import GymnosDataGenerator_i2 as gen
import HelperFunctions_i2 as helper

Using TensorFlow backend.


---
## Create a labels and partitions CSV


In [0]:
csv_location = "/content/drive/My Drive/GYMNOS/Video Dataset/"
labels_location = "/content/drive/My Drive/GYMNOS/Video Dataset/labels.csv"
partitions_location = "/content/drive/My Drive/GYMNOS/Video Dataset/partitions.csv"
ohp_down_reps_location = "/content/drive/My Drive/GYMNOS/Video Dataset/Overhead Press/repetitions/Down/"
ohp_up_reps_location = "/content/drive/My Drive/GYMNOS/Video Dataset/Overhead Press/repetitions/Up/"

ohp_down_label = 0
ohp_up_label = 1

In [0]:
helper.init_labels_csv(labels_location)

In [0]:
# Label the ohp down motion
helper.append_to_labels_csv(labels_location, ohp_down_reps_location, ohp_down_label)

# Label the ohp up motion
helper.append_to_labels_csv(labels_location, ohp_up_reps_location, ohp_up_label)

In [0]:
helper.generate_partitions_csv(partitions_location, labels_location)

---
## Read in the labels and partitions CSVs


In [0]:
partition_location = "/content/drive/My Drive/GYMNOS/Video Dataset/partitions.csv"
labels_location = "/content/drive/My Drive/GYMNOS/Video Dataset/labels.csv"

partition = helper.read_partition_csv(partition_location)
labels = helper.read_labels_csv(labels_location)

In [0]:
print(len(partition["train"]))
print(len(partition["validation"]))
print(len(partition["test"]))

In [0]:
# '/content/drive/My Drive/GYMNOS/Video Dataset/Overhead Press/repetitions/Up/video 1.19.10.MOV'
test_data = ['/content/drive/My Drive/GYMNOS/Video Dataset/Overhead Press/repetitions/Up/video 1.19.10.MOV', 
             '/content/drive/My Drive/GYMNOS/Video Dataset/Overhead Press/repetitions/Down/video 1.23.21.MOV']

In [0]:
pre_train_params = {'frame_strides': 1,
                    'batch_size': 2,
                    'n_classes': 2,
                    'shuffle': True}

pre_train_generator = gen.DataGenerator(test_data, labels, **pre_train_params)

In [0]:
testing_x, testing_y = pre_train_generator.__getitem__(0)

In [0]:
testing_x.shape

In [0]:
helper.show_images(testing_x[1])

In [0]:
print(testing_y[1])

--- 
## Initialize the DataGenerator

In [0]:
import matplotlib.pyplot as plt

In [0]:
train_params = {'frame_strides': 1,
                'batch_size': 64,
                'n_classes': 2,
                'shuffle': True}

val_params = {'frame_strides': 1,
              'batch_size': 3,
              'n_classes': 2,
              'shuffle': True}

train_generator = gen.DataGenerator(partition["train"], labels, **train_params)
val_generator = gen.DataGenerator(partition["validation"], labels, **val_params)

In [47]:
train_generator.__len__()

0

In [0]:
vid_frames, vid_labels = train_generator.__getitem__(0)

In [0]:
print(vid_frames.shape)
print(vid_labels.shape)

(5, 16, 112, 112, 3)
(5, 2)


In [0]:
print(vid_labels[0])

[0. 1.]


In [0]:
helper.show_images(vid_frames[0])

In [0]:
import numpy as np
from keras.utils.data_utils import get_file

---
## Model Imports

In [0]:
import tensorflow as tf
from tensorflow.keras.models import Sequential, Model
from tensorflow.keras.layers import Conv3D
from tensorflow.keras.layers import MaxPooling3D
from tensorflow.keras.layers import ZeroPadding3D
from tensorflow.keras.layers import Flatten
from tensorflow.keras.layers import Dense
from tensorflow.keras.layers import Input
from tensorflow.keras.layers import Dropout
from tensorflow.keras import optimizers
from tensorflow.keras.models import load_model
from keras.utils.data_utils import get_file

---
## Create the model


In [0]:
# Create C3D Model 
def create_gymnos_model():
    # Recreate the first few layers of the C3D network
    model = Sequential()
    c3d_weights_location = '/content/drive/My Drive/GYMNOS/Product Development/Implementation Details/Gymnos_i2/C3D_Sport1M_weights_keras_2.2.4.h5'
    WEIGHTS_PATH = 'https://github.com/adamcasson/c3d/releases/download/v0.1/sports1M_weights_tf.h5'
    
    input_shape = (16, 112, 112, 3)
    # 1st layer group
    model.add(Conv3D(64, (3, 3, 3), activation='relu',
                     padding='same', name='conv1',
                     input_shape=input_shape))
    model.add(MaxPooling3D(pool_size=(1, 2, 2), strides=(1, 2, 2),
                           padding='valid', name='pool1'))
    # 2nd layer group
    model.add(Conv3D(128, (3, 3, 3), activation='relu',
                     padding='same', name='conv2'))
    model.add(MaxPooling3D(pool_size=(2, 2, 2), strides=(2, 2, 2),
                           padding='valid', name='pool2'))
    # 3rd layer group
    model.add(Conv3D(256, (3, 3, 3), activation='relu',
                     padding='same', name='conv3a'))
    model.add(Conv3D(256, (3, 3, 3), activation='relu',
                     padding='same', name='conv3b'))
    model.add(MaxPooling3D(pool_size=(2, 2, 2), strides=(2, 2, 2),
                           padding='valid', name='pool3'))
    # 4th layer group
    model.add(Conv3D(512, (3, 3, 3), activation='relu',
                     padding='same', name='conv4a'))
    model.add(Conv3D(512, (3, 3, 3), activation='relu',
                     padding='same', name='conv4b'))
    model.add(MaxPooling3D(pool_size=(2, 2, 2), strides=(2, 2, 2),
                           padding='valid', name='pool4'))
    # 5th layer group
    model.add(Conv3D(512, (3, 3, 3), activation='relu',
                     padding='same', name='conv5a'))
    model.add(Conv3D(512, (3, 3, 3), activation='relu',
                     padding='same', name='conv5b'))
    model.add(ZeroPadding3D(padding=((0, 0), (0, 1), (0, 1)), name='zeropad5'))
    model.add(MaxPooling3D(pool_size=(2, 2, 2), strides=(2, 2, 2),
                           padding='valid', name='pool5'))
    model.add(Flatten())
    # FC layers group
    model.add(Dense(4096, activation='relu', name='fc6'))
    model.add(Dense(4096, activation='relu', name='fc7'))
    
    model.add(Dense(2, activation='sigmoid'))

    # Load in pre-trained weights
    model.load_weights(c3d_weights_location, by_name=True)
    #weights_path = get_file('sports1M_weights_tf.h5',
    #                    WEIGHTS_PATH,
    #                    cache_subdir='models',
    #                    md5_hash='b7a93b2f9156ccbebe3ca24b41fc5402')

    #model.load_weights(weights_path, by_name=True)
    
    # Freeze first 4 layers
    for layer in model.layers[:-2]:
      layer.trainable = False
      
    model.compile(optimizer=optimizers.RMSprop(lr=0.1), 
                         loss="binary_crossentropy",
                         metrics=['acc'])
    return model

In [0]:
# Create Gymnos model
gymnos_model = create_gymnos_model()

In [50]:
gymnos_model.summary()

Model: "sequential_6"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
conv1 (Conv3D)               (None, 16, 112, 112, 64)  5248      
_________________________________________________________________
pool1 (MaxPooling3D)         (None, 16, 56, 56, 64)    0         
_________________________________________________________________
conv2 (Conv3D)               (None, 16, 56, 56, 128)   221312    
_________________________________________________________________
pool2 (MaxPooling3D)         (None, 8, 28, 28, 128)    0         
_________________________________________________________________
conv3a (Conv3D)              (None, 8, 28, 28, 256)    884992    
_________________________________________________________________
conv3b (Conv3D)              (None, 8, 28, 28, 256)    1769728   
_________________________________________________________________
pool3 (MaxPooling3D)         (None, 4, 14, 14, 256)   

In [0]:
# If you stop mid training save it here
mid_training = "/content/drive/My Drive/GYMNOS/Product Development/Implementation Details/Gymnos_i2/gymnos_mid_training.h5"
gymnos_model.save(mid_training)

In [0]:
# Load model that was stopped mid training
gymnos_model = load_model(mid_training)

In [51]:
# Create the tensorBoard callback
logdir = os.path.join("logs", datetime.datetime.now().strftime("%Y%m%d-%H%M%S"))
tensorboard_callback = tf.keras.callbacks.TensorBoard(logdir, histogram_freq=1)

history = gymnos_model.fit_generator(pre_train_generator, 
                                     steps_per_epoch=pre_train_generator.__len__(), 
                                     epochs=5, 
                                     shuffle=True)

Epoch 1/5
1/1 [==============================] - 5s 5s/step - loss: 0.6908 - acc: 0.5000
Epoch 2/5
1/1 [==============================] - 4s 4s/step - loss: 0.0000e+00 - acc: 1.0000
Epoch 3/5
1/1 [==============================] - 4s 4s/step - loss: 0.0000e+00 - acc: 1.0000
Epoch 4/5
1/1 [==============================] - 4s 4s/step - loss: 0.0000e+00 - acc: 1.0000
Epoch 5/5
1/1 [==============================] - 3s 3s/step - loss: 0.0000e+00 - acc: 1.0000


In [52]:
gymnos_model.predict_generator(pre_train_generator)

array([[1., 0.],
       [0., 1.]], dtype=float32)

In [0]:
# Saved the finished model after training
finished_model = "/content/drive/My Drive/GYMNOS/Product Development/Implementation Details/Gymnos_i2/gymnos_finished_i1.h5"
gymnos_model.save(finished_model)

---
## TensorBoard Training Visualization

In [0]:
# Run before you fit the model
%tensorboard --logdir logs

---
## Evaluating the Model
Now that the Model has it's weights initialized, let see how it performs on the test set.

In [0]:
trained_model = load_model(iteration_1_location)

In [0]:
# Parameters
params = {'data_location': "/content/drive/My Drive/GYMNOS/Video Dataset/Frames/",
          'dim': (224, 224, 3),
          'batch_size': 64,
          'n_classes': 2,
          'shuffle': True}

test_generator = gen.DataGenerator(partition["test"], labels, **params)

In [0]:
images, pred_class = test_generator.__getitem__(0)

In [0]:
helper.show_images(images)

In [0]:
model_predictions = trained_model.predict_classes(images)

In [0]:
for index, number in enumerate(model_predictions):
  if number == 0:
    print("Image("+ str(index + 1) + ") is a squat")
  else:
    print("Image("+ str(index + 1) + ") is a overheadpress")